# This is a notebook quickly exploring different BSS methods used on our datasets

## Imports: 

In [36]:
import numpy as np
import scipy
from matplotlib import pyplot as plt
import soundfile as sf
import os
import IPython
from einops import rearrange

import pyroomacoustics

## Obtaining the sound samples:

In [37]:
samples_directory = 'sound_samples/'
sample_list = os.listdir(samples_directory)
sample_list

['4kHz_sin_wave.wav',
 'free-flight_whitenoise.wav',
 'music_example0.wav',
 'original.wav',
 'rotors.wav',
 'rotors_and_4kHz_sin_wave.wav',
 'rotors_and_speech.wav',
 'silent-flight_whitenoise.wav']

In [92]:
file = samples_directory + sample_list[2]
n_src = 4
file, n_src

('sound_samples/music_example0.wav', 4)

In [93]:
audio, sample_rate = sf.read(file)
audio = audio.T
(audio.shape, sample_rate)

((2, 220500), 44100)

In [94]:
IPython.display.Audio(audio, rate=sample_rate)

In [95]:
nfft = 1024
nperseg = 256
max_len = 2048
f, t, Yxx = scipy.signal.stft(audio, nperseg=nperseg, nfft=nfft)
if Yxx.shape[2] > max_len:
    Yxx = Yxx[:, :, :max_len]
Yxx.shape, Yxx.dtype

((2, 513, 1724), dtype('complex128'))

In [96]:
# sanity check - is the restored signal good?
t, restored_audio = scipy.signal.istft(Yxx, nperseg=nperseg, nfft=nfft)
restored_audio.shape

(2, 220544)

In [97]:
IPython.display.Audio(restored_audio, rate=sample_rate)

## FAST-MNMF

In [98]:
# matching the input as required
# documentation at
# https://pyroomacoustics.readthedocs.io/en/pypi-release/pyroomacoustics.bss.html
X = rearrange(Yxx, 'channel freq frame -> frame freq channel')
X_sep = pyroomacoustics.bss.fastmnmf(X, n_src=n_src)
# notice that the function has a lot of optional hyper parameters, might be used for this

In [99]:
X_sep = rearrange(X_sep, 'frame freq source -> source freq frame')
X_sep.shape

(4, 513, 1724)

In [100]:
t, audio_sep = scipy.signal.istft(X_sep, nperseg=nperseg, nfft=nfft)
audio_sep.shape

(4, 220544)

In [110]:
IPython.display.Audio(audio_sep[3], rate=sample_rate, autoplay=True)

## AuxIVA:

In [111]:
#This should be True
# X.shape == (603, 513, 6)
X.shape

(1724, 513, 2)

In [116]:
Y = pyroomacoustics.bss.auxiva(X, n_src=np.min([n_src, X.shape[2]]))
Y = rearrange(Y, 'frame freq source -> source freq frame')
t, y = scipy.signal.istft(Y, nperseg=nperseg, nfft=nfft)
y.shape

(2, 220544)

In [120]:
IPython.display.Audio(y[1], rate=sample_rate, autoplay=True)

## Trincon - time domain

In [114]:
signals = audio
max_audio_len = 220500
if signals.shape[1] > max_audio_len:
    signals = signals[:, :max_audio_len]
Y_tricon = pyroomacoustics.bss.trinicon(signals)
Y_tricon.shape

(2, 222546)

In [122]:
IPython.display.Audio(Y_tricon[1], rate=sample_rate)

## ILRMA

In [123]:
Y_ilrma = pyroomacoustics.bss.ilrma(X)
Y_ilrma.shape

(1724, 513, 2)

In [124]:
Y_ilrma = rearrange(Y_ilrma, 't f c -> c f t')
t, y_ilrma = scipy.signal.istft(Y_ilrma, nperseg=nperseg, nfft=nfft)
y_ilrma.shape

(2, 220544)

In [127]:
IPython.display.Audio(y_ilrma[1], rate=sample_rate, autoplay=True)

In [71]:
IPython.display.Audio(y_ilrma[1], rate=sample_rate)

## SparseAuxIVA:
* This will not be looked into because it uses the $S$ sparcity matrix for frequancy bins

## Summery:
* original - AuxIVA, ILRMA worked well
* white noise & free flight - all seeped to silance the noise, some(Fast MNMF) to seperate wind and rotors
* sin wav + rotors - only the AuxIVa seems to work right, and maybe the ILRMA, and maybe FAST-MNMF(may need some adjastments)